![EncabezadoIN](EncabezadoIN.JPG)

## Laboratorio 2 - Regresión

Integrantes: 
Juan Pablo Lora Hernández - 202012524 

Andrés Francisco Borda Rincón - 201729184

Gabriela Vargas Rojas - 202013830


## Caso 
CompuAlpes es una reconocida tienda minorista que vende computadores portátiles de diferentes fabricantes y especificaciones técnicas. Con el auge de la tecnología y el creciente número de productos en el mercado, la empresa busca optimizar sus estrategias de fijación de precios y promociones para seguir siendo competitiva. Es en este último punto, donde ha identificado un reto relacionado con determinar el precio adecuado para un portatil ya que el mercado es dinámico y la valoración de las características técnicas cambia con el tiempo. Poner un precio demasiado alto puede alejar a los clientes, mientras que ponerlo demasiado bajo puede reducir los márgenes de ganancia.
Esto motivó a CompuAlpes a proponer el objetivo de este proyecto, en el cual se desea construir un modelo de regresión que permita estimar el precio de un portátil a partir de sus especificaciones técnicas, determinando las que más impactan en el precio o que son, de acuerdo a la evidencia, irrelevantes para la estimación. Este modelo permitirá a CompuAlpes tener una base objetiva y cuantitativa al momento de establecer precios para sus productos.

### Participación individual

Todos los apartados del desarrollo del caso fueron realizados por partes iguales por los tres integrantes del grupo en vez de dividirlo como esta planteado en la rubrica. Por esto consideramos que todos deben ser incluidos en todos los apartados.

## 1. Carga de librerías necesarias para implementación

In [1]:
import numpy as np
import pandas as pd

from joblib import dump, load

import matplotlib.pyplot as plt
import seaborn as sns; sns.set()  # for plot styling

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import PolynomialFeatures
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.base import BaseEstimator, TransformerMixin


from matplotlib import cm
from mpl_toolkits.mplot3d import Axes3D # for 3D plots

import scipy.stats as stats

## 2. Cargar los datos

In [2]:
# Se cargan los datos de entrenamiento.
df_compu=pd.read_csv('./Regresión_data_laptop_data_train.csv', sep=',', encoding = "ISO-8859-1")

## 3. Entendimiento de los datos 

Al explorar los datos encontramos que nos dieron registros de 1216 computadores que se han venido en la tienda minorista de CompuAlpes de diferentes fabricantes y especificaciones técnicas. Cada registro cuenta con 14 columnas de las cuales 7 son numéricas y 7 son categóricas. De estas, 1 columna nos sirve para identificar cada uno de manera única, 10 nos dan información sobre las características o especificaciones técnicas sobre los computadores y las últimas 3 nos dan informacion sobre los fabricantes involucrados en diferentes componentes de estos.

Respecto al diccionario de datos proporcionado, este no contiene los rangos de valores que pueden manejar las variables númericas por ende se hace más díficil el análisis en términos de validez.
Aún así, se realizan los respecrtivos analisis estadisticos de variables númericas.

In [3]:
df_compu.shape

(1216, 14)

In [4]:
df_compu.dtypes

id               int64
Company         object
TypeName        object
Ram              int64
Weight         float64
Price          float64
TouchScreen      int64
Ips              int64
Ppi            float64
Cpu_brand       object
HDD            float64
SSD              int64
Gpu_brand       object
Os              object
dtype: object

In [5]:
df_compu.sample(5)

id Company     TypeName  Ram  Weight      Price  TouchScreen  Ips  \
832    736      HP  Workstation   16    2.60  11.766671            0    0   
1086    94    Asus    Ultrabook    8    1.25  10.931154            0    0   
536    369      HP    Ultrabook    8    1.36  11.442932            0    1   
673   1246    Asus       Gaming   16    2.34  11.727036            0    1   
806   1272      HP     Notebook    6    2.19  10.614129            0    0   

             Ppi      Cpu_brand     HDD  SSD Gpu_brand       Os  
832   141.211998  Intel Core i7     0.0  256    Nvidia  Windows  
1086  157.350512  Intel Core i7     0.0  256     Intel  Windows  
536   157.350512  Intel Core i7     0.0  256     Intel  Windows  
673   141.211998  Intel Core i7  1000.0  256    Nvidia  Windows  
806   100.454670  Intel Core i7  1000.0    0       AMD  Windows

In [6]:
#Analisis estadistico de las variables numericas
df_compu_num = df_compu[['id', 'Ram', 'Weight', 'Ppi', 'HDD', 'SSD', "Price"]].copy()
df_compu_num.describe()

id          Ram       Weight          Ppi           HDD  \
count  1216.000000  1216.000000  1193.000000  1204.000000   1200.000000   
mean    637.925164     8.458882     2.401572   183.830716    441.218800   
std     367.482876     5.094332     4.844791   449.708876    927.052855   
min       0.000000     2.000000     0.690000    90.583402      0.000000   
25%     319.750000     4.000000     1.500000   127.335675      0.000000   
50%     638.500000     8.000000     2.040000   141.211998      0.000000   
75%     954.250000     8.000000     2.320000   157.350512   1000.000000   
max    1272.000000    64.000000    97.729949  7328.468865  24127.543112   

               SSD        Price  
count  1216.000000  1201.000000  
mean    187.529605    13.114402  
std     186.902926    28.659102  
min       0.000000     9.134616  
25%       0.000000    10.403650  
50%     256.000000    10.882316  
75%     256.000000    11.288115  
max    1024.000000   499.766079

## 4. Analisis de calidad de los datos

### 4.1 Completitud

In [7]:
#Sacamos las variables candidatas
features = ["Company", "TypeName", "Ram", "Weight", "TouchScreen", "Ips", "Ppi", "Cpu_brand", "HDD", "SSD", "Gpu_brand", "Os"]

In [8]:
#Analizamos la completitud de los datos
df_compu[["Price"]+features].isnull().sum() / df_compu.shape[0]

Price          0.012336
Company        0.000000
TypeName       0.000000
Ram            0.000000
Weight         0.018914
TouchScreen    0.000000
Ips            0.000000
Ppi            0.009868
Cpu_brand      0.000000
HDD            0.013158
SSD            0.000000
Gpu_brand      0.000000
Os             0.000000
dtype: float64

Para el análisis de completitud se vio que porcentaje de valores nulos tiene cada una de las columnas de los datos. Se encontró que 9 de las columnas están completas mientras que en las demás se encontraron algunos nulos. 

### 4.2 Unicidad

In [9]:
#Se revisa si hay registros duplicados
df_compu.duplicated(keep = False).sum()

10

Para el análisis de unicidad primero se buscó si había registros repetidos y se encontró que existen 10 registros que están duplicados.

### 4.3 Consistencia

Se encontró que la columnas de “Type name” y "GPU brand" cuentan con valores similares a otros y probablemente son errores de digitación.

In [10]:
# Se revisa la variable TypeName
df_compu.TypeName.value_counts()

Notebook                656
Gaming                  189
Ultrabook               187
2 in 1 Convertible      109
Workstation              29
Netbook                  21
Notebook%%                9
&&Notebook                5
Gaming%%                  4
&&Gaming                  3
&&2 in 1 Convertible      2
2 in 1 Convertible%%      1
&&Ultrabook               1
Name: TypeName, dtype: int64

In [11]:
# Se revisa la variable GPU Brand
df_compu.Gpu_brand.value_counts()

Intel       662
Nvidia      371
AMD         166
Intel%%       6
Nvidia%%      6
&&Intel       2
&&Nvidia      1
AMD%%         1
&&AMD         1
Name: Gpu_brand, dtype: int64

Dado que no se dieron posibles valores en el diccionario de datos para las variables numericas estas no pueden ser revisadas.

### 4.4 Validez

Se reviso la validez de cada columna y no se encontraron valores fuera de lo normal para ninguna. Esto puede ser evidenciado en que en la carga de los datos todas las columnas son del datatype esperado. Adicionalmente, se cargaron los datos en la herramienta Power BI y no se encontro errores en ninguna columna.

## 5. Perfilamiento de datos

A continuacion se presenta un perfilamiento completo de los datos con el perfilador Pandas Profiling para un entendimiento mayor de los datos

In [12]:
import pandas_profiling

profiling =pandas_profiling.ProfileReport(df_compu)
profiling

C:\Users\andre\AppData\Local\Temp\ipykernel_12056\2046165207.py:1: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  import pandas_profiling


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## 6. Preparación de los datos 

### 6.1 Correción de los datos

Se determino que la mejor estrategia para corregir los valores nulos es la de eliminar esos registros dado que son muy pocos y ademas muchos de los registros con nulos cunetan con valores que tambien tienen errores de digitacion en otras columnas.

In [13]:
#Eliminar las filas con valores nulos
df_compu_prep = df_compu.dropna()
df_compu_prep[["Price"]+features].isnull().sum() / df_compu_prep.shape[0]

Price          0.0
Company        0.0
TypeName       0.0
Ram            0.0
Weight         0.0
TouchScreen    0.0
Ips            0.0
Ppi            0.0
Cpu_brand      0.0
HDD            0.0
SSD            0.0
Gpu_brand      0.0
Os             0.0
dtype: float64

In [14]:
# Eliminar registros duplicados y quedarse con uno de cada conjunto de duplicados
#Problema de duplicidad
df_compu_prep.drop_duplicates(inplace=True)
#Se revisa si hay registros duplicados
df_compu_prep.duplicated(keep = False).sum()


C:\Users\andre\AppData\Local\Temp\ipykernel_12056\3772055880.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_compu_prep.drop_duplicates(inplace=True)


0

Para los errores de consistencia se corrigen los valores que tienen errores de digitación para añadirlos a su categoria correcta.

In [15]:
#Problema de consistencia columna (TypeName)
def corregir_TypeName(variacion):
    if variacion in ["Notebook%%", "&&Notebook"]:
        return "Notebook"
    elif variacion in ["Gaming%%", "&&Gaming"]:
        return "Gaming"
    elif variacion in ["&&2 in 1 Convertible", "2 in 1 Convertible%%"]:
        return "2 in 1 Convertible"
    elif variacion in ["&&Ultrabook"]:
        return "Ultrabook"
    else:
        return variacion

# Aplicar la función a la columna titleType
df_compu_prep['TypeName'] = df_compu_prep['TypeName'].apply(corregir_TypeName)

# Verificar nuevamente la variable titleType después de corregir
df_compu_prep.TypeName.value_counts()

C:\Users\andre\AppData\Local\Temp\ipykernel_12056\3083795587.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_compu_prep['TypeName'] = df_compu_prep['TypeName'].apply(corregir_TypeName)


Notebook              644
Gaming                192
Ultrabook             177
2 in 1 Convertible    106
Workstation            28
Netbook                19
Name: TypeName, dtype: int64

In [16]:
# Se revisa la variable TypeName
df_compu.Gpu_brand.value_counts()

Intel       662
Nvidia      371
AMD         166
Intel%%       6
Nvidia%%      6
&&Intel       2
&&Nvidia      1
AMD%%         1
&&AMD         1
Name: Gpu_brand, dtype: int64

In [17]:
#Problema de consistencia columna (Gpu_brand)
def corregir_Gpu_brand(variacion):
    if variacion in ["Intel%%", "&&Intel"]:
        return "Intel"
    elif variacion in ["Nvidia%%", "&&Nvidia"]:
        return "Nvidia"
    elif variacion in ["&&AMD", "AMD%%"]:
        return "AMD"
    else:
        return variacion

# Aplicar la función a la columna titleType
df_compu_prep['Gpu_brand'] = df_compu_prep['Gpu_brand'].apply(corregir_Gpu_brand)

# Verificar nuevamente la variable titleType después de corregir
df_compu_prep.Gpu_brand.value_counts()

C:\Users\andre\AppData\Local\Temp\ipykernel_12056\441937007.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_compu_prep['Gpu_brand'] = df_compu_prep['Gpu_brand'].apply(corregir_Gpu_brand)


Intel     637
Nvidia    369
AMD       160
Name: Gpu_brand, dtype: int64

Como sabemos el modelo de regresión es sensible a valores atipicos por lo que revisamos los valores atipicos en la variable de interes y en los candidatos a elegir para la regression y los eliminamos.

In [18]:
# Analizar valores atipicos en la variable de interes

df_compu_prep_var = df_compu_prep[['Price']].copy()
fig=plt.figure(figsize=(20,8))
ax = sns.boxplot(data=df_compu_prep_var, orient ="v")

In [19]:
#Eliminar los outliers price
Q1 = df_compu_prep['Price'].quantile(0.25)
Q3 = df_compu_prep['Price'].quantile(0.75)
IQR = Q3 - Q1

# Define lower and upper bounds
lower_bound = Q1 - 1.5 * IQR
upper_bound = Q3 + 1.5 * IQR
df_compu_prep = df_compu_prep[(df_compu_prep['Price'] >= lower_bound) & (df_compu_prep['Price'] <= upper_bound)]

In [20]:
# Analizar valores atipicos en la variable RAM

df_compu_prep_var = df_compu_prep[['Ram']].copy()
fig=plt.figure(figsize=(20,8))
ax = sns.boxplot(data=df_compu_prep_var, orient ="v")

In [21]:
#Eliminar los outliers de la variable Ram
Q1 = df_compu_prep['Ram'].quantile(0.25)
Q3 = df_compu_prep['Ram'].quantile(0.75)
IQR = Q3 - Q1

# Define lower and upper bounds
lower_bound = Q1 - 1.5 * IQR
upper_bound = Q3 + 1.5 * IQR
df_compu_prep = df_compu_prep[(df_compu_prep['Ram'] >= lower_bound) & (df_compu_prep['Ram'] <= upper_bound)]

Ahora, se realizara un analisis para verificar la relación de las diferentes variables con la variable objetivo separado entre las variables categoricas y las numericas.

In [22]:
#Sacamos las variables numericas y categoricas
features_num = ["Ram", "Weight", "Ppi", "HDD", "SSD"]
features_cat = ["Company", "TypeName", "TouchScreen", "Ips", "Cpu_brand", "Gpu_brand", "Os"]

In [23]:
#Relación de la variable objetivo con las demas variables
sns.pairplot(df_compu_prep.sample(frac=0.2), height=4, y_vars="Price", x_vars=features_num, kind="scatter")

In [24]:
#Relación de la variable objetivo con las demas variables
sns.pairplot(df_compu_prep.sample(frac=0.2), height=4, y_vars="Price", x_vars=features_cat, kind="scatter")

Revisamos preventivamente las correlaciones entre las variables explicativas para ayudar al proceso de seleccion.

In [25]:
# Correlaciones
plt.figure(figsize=(12, 10))
sns.heatmap(df_compu_prep[features_num].corr(), cmap="Blues", vmin=0, vmax=1)

<AxesSubplot:>

Se construira un Label Encoder para pasar la variable CPU Brand a numerica. Se decide utilizar este metodo dado que esta variable es ordinal dado que mietras mejor sea el procesador mayor es el precio del computador.

In [26]:
#Pasar la variable procesador a numerica utilizando label encoder
label_encoder = LabelEncoder()
custom_order = {'Other Intel Processor': 0, 'AMD Processor': 1, 'Intel Core i3': 2, 'Intel Core i5': 3, 'Intel Core i7': 4}

df_compu_prep['Cpu_brand_encoded'] = df_compu_prep['Cpu_brand'].map(custom_order)
df_compu_prep.Cpu_brand.value_counts()

Intel Core i5            376
Intel Core i7            285
Intel Core i3            124
Other Intel Processor    119
AMD Processor             53
Name: Cpu_brand, dtype: int64

In [27]:
sns.pairplot(df_compu_prep.sample(frac=0.2), height=4, y_vars="Price", x_vars="Cpu_brand_encoded", kind="scatter")

Adicionalmente, tambien se decidio utilizar la varianble Ram como una variable categorica dado que no es una variable continua por lo que se ajusta mejor a modelarla como una categorica. 

In [28]:
#Pasar la variable Ram a categorica
custom_order = {2: 0, 4: 1, 6: 2, 8: 3, 12: 4, 16: 5, 24: 6, 32: 7, 64: 8}

df_compu_prep['Ram_encoded'] = df_compu_prep['Ram'].map(custom_order)
df_compu_prep.Ram.value_counts()

8     558
4     329
6      33
12     24
2      13
Name: Ram, dtype: int64

In [29]:
sns.pairplot(df_compu_prep.sample(frac=0.2), height=4, y_vars="Price", x_vars="Ram_encoded", kind="scatter")

## 7. Entrenamiento del modelo

### 7.1 Selección de variables

Dados los resultados presentados anteriormente, se determino que las dos variables a utilizar son "Cpu_brand" y "Ram". Esta eleccion se hizo dado que son las unicas dos variables que muestran una relación lineal con las variable objetivo. Para la verificación del modelo se dividiran los datos en train y test.

In [30]:
#Se copian las variables a utilizar
var_selec = ["Cpu_brand_encoded", "Ram_encoded"]
#df_compu_model_X = df_compu_prep[var_selec].copy()
#df_compu_model_Y = df_compu_prep["Price"].copy()
X_train, X_test, y_train, y_test = train_test_split(df_compu_prep[var_selec], df_compu_prep["Price"], test_size=0.3, random_state=1)

In [31]:
X_train.shape, y_train.shape

((669, 2), (669,))

In [32]:
X_test.shape, y_test.shape

((288, 2), (288,))

Para obtener un mejor modelo, se decidio utilizar un Standar Scaler para estandarizar las variables explicativas y traerlas a un mismo rango y magnitud.

In [33]:
# Vamos a llevar al mismo dominio las diferentes variables
mms= StandardScaler()
# transform data
df_compu_Xnorm = mms.fit_transform(X_train[var_selec])
df_compu_model_X = pd.DataFrame(df_compu_Xnorm, columns =var_selec)

### 7.2 Entrenamiento del modelo

In [34]:
# Se entrena el modelo con los datos de entrenamiento elegidos
regression = LinearRegression()
regression.fit(df_compu_model_X, y_train)

LinearRegression()

In [35]:
Una vez calculada la regresión extraemos los valores para la coeficientes de nuestras variables explicativas y el intercepto de la función

SyntaxError: invalid syntax (1892082035.py, line 1)

In [ ]:
pd.DataFrame({"columns": var_selec, "coef": regression.coef_})

In [ ]:
regression.intercept_

En los resultados podemos observar que la marca del CPU del computador tiene un coeficiente de 0.244 y la cantidad que tiene de Ram un 0.241. Esto indica que como era de esperar ambas variables tienen una relación positiva con la variable de interes. Por el otro lado como el intercepto es de 10.68 sabemos que este es el minimo precio que pueden tener los computadores. En las siguientes graficas podemos apreciar como las variables se ajustan a la relacion lineal encontrada con la regresión. 

In [ ]:
f, axs = plt.subplots(1, len(var_selec), sharey=True, figsize=(20, 4))

for i in range(len(var_selec)):
    col = var_selec[i]
    x = X_train[col]
    m = regression.coef_[i]
    b = regression.intercept_

    axs[i].plot(x, y_train, "o", alpha=0.1)
    axs[i].plot(x, x * m + b)
    axs[i].set_title(col)

Cualitativamente, podemos afirmar que el modelo calculado tiene el comportamiento esperado segun las variables seleccionadas y nos da una buena intuición de como se comporta el precio de los computadores segun estas variables. Para esta validación se hara uso del set de datos test reservado anteriormente.

## 8. Validación del modelo

Para la validacion del modelo se utilizaran distintas medidas de error.

**Mean Absolute Error (MAE)**

$$ MAE = {1 \over n}{\sum_{i=1}^n {|y_{i} - y_{i}'|} } $$

In [ ]:
# Calculo del error MAE
print("Train:", mean_absolute_error(y_train, regression.predict(df_compu_model_X)))
print("Test:", mean_absolute_error(y_test, regression.predict(X_test)))

Como podemos observar esta medida de error nos arroja un resultado muy bueno para los datos de entrenamiento y relativamente bueno para los datos de prueba. Aunque el error en los datos de prueba podria ser más bajo, consideramos que la metrica es buena considerando el rango de la variable de interes.

**Root Mean Squeared Error (RMSE)**

$$ RMSE = {1 \over n}{\sum_{i=1}^n {(y_{i} - y_{i}')^2} } $$

In [ ]:
print("Train:", np.sqrt(mean_squared_error(y_train, regression.predict(df_compu_model_X))))
print("Test:", np.sqrt(mean_squared_error(y_test, regression.predict(X_test))))

Igual que con el MAE el RMSE nos arroja un resultado muy similar mostrando que el modelo entrenado da una muy buena metrica para los datos de prueba y un resultado aceptable para los datos de entrenamiento. 

**Análisis del error**

In [ ]:
plt.figure(figsize=(20, 3))
sns.boxplot(x=y_test, showmeans=True, orient="h")
plt.title("Valor real de $\t{Price}$ en el conjunto de prueba")
plt.grid()
plt.show()

In [ ]:
y_test.describe(percentiles=[0.25, 0.5, 0.75, 0.99])

In [ ]:
plt.figure(figsize=(20, 3))
sns.boxplot(x=abs(y_test - regression.predict(X_test)), showmeans=True, orient="h")
plt.title("|Valor real - Valor estimado| de $\t{Price}$")
plt.xlabel("Error")
plt.grid()
plt.show()

In [ ]:
abs(y_test-regression.predict(X_test)).describe(percentiles=[0.25, 0.5, 0.75, 0.95, 0.99])

Dados los resultados cuantitativos podeos afirmar que el modelo es bueno para predecir los precios dado que la magnitud del error es buena. Consideramos que con mas información el modelo planteado podria ser mejorado significativamente ya que podria usar aun mas datos para el set de pruebas llevando a un resultado más completo. 

## 9. Supuestos

### 9.1. Colinealidad

In [ ]:
plt.figure(figsize=(12, 10))
sns.heatmap(X_train.corr(), cmap="Blues", vmin=0, vmax=1)

In [ ]:
X_train.corr()

Se puede ver en la gráfica que las variables tienen una relación, sin embargo, el coeficiente es de 0,5862 lo cual indica que es baja y se pueden usar.

### 9.2. Linealidad

In [ ]:
sns.pairplot(pd.concat([X_train, y_train], axis=1), height=4, y_vars="Price", x_vars=var_selec, kind="scatter")

Como podemos observar la relación de las variables elegidas con la variable objetivo es lineal por lo que se cumple el supuesto.

### 9.3. Normalidad de Errores

In [ ]:
errors = (regression.predict(X_train[var_selec])-y_train).values

In [ ]:
fig, axes = plt.subplots(1, 2, figsize=(12, 4))

# Dispersión
sns.scatterplot(x=regression.predict(X_train[var_selec]), y=errors, alpha=0.1, ax=axes[0])

# q-q plot
_ = stats.probplot(errors, dist="norm", plot=axes[1])

Podemos observar en la grafica qq-plot como la distribución de los errores se ajusta bien a la distribución normal por lo que se cumple el supuesto de normalidad de los errores.

### 9.4. Homocedasticidad

In [ ]:
sns.scatterplot(x = regression.predict(X_train[var_selec]), y=errors, alpha=0.1)

En la distribución se puede ver que no existe un problema de heterocedasticidad.

## 10. Pipeline

Dado el modelo encontrado previamente encontrado se realizo un pipeline que automatice todos los pasos de procesamiento, eleccion de variables y calculo de la regresión. 

In [ ]:
class CustomPreprocessor(BaseEstimator, TransformerMixin):
    def init(self):
        pass

    def fit(self, X, y=None):
        return self

    def transform(self, X):

        X_processed = X.copy()  # Cambia df_compu.copy() a X.copy()
        #Quitar nulos
        X_processed = X_processed.dropna()
        #Quitar duplicados
        X_processed.drop_duplicates(inplace=True)

        #Quitar outliers de la variable objetivo
        Q1 = X_processed['Price'].quantile(0.25)
        Q3 = X_processed['Price'].quantile(0.75)
        IQR = Q3 - Q1

        # Define lower and upper bounds
        lower_bound = Q1 - 1.5 * IQR
        upper_bound = Q3 + 1.5 * IQR
        X_processed = X_processed[(X_processed['Price'] >= lower_bound) & (X_processed['Price'] <= upper_bound)]

        #Quitar outliers de la variable RAM
        Q1 = X_processed['Ram'].quantile(0.25)
        Q3 = X_processed['Ram'].quantile(0.75)
        IQR = Q3 - Q1

        # Define lower and upper bounds
        lower_bound = Q1 - 1.5 * IQR
        upper_bound = Q3 + 1.5 * IQR
        X_processed = X_processed[(X_processed['Ram'] >= lower_bound) & (X_processed['Ram'] <= upper_bound)]

        #Encoder de la variable CPU Brands
        custom_order = {'Other Intel Processor': 0, 'AMD Processor': 1, 'Intel Core i3': 2, 'Intel Core i5': 3, 'Intel Core i7': 4}
        X_processed['Cpu_brand_encoded'] = X_processed['Cpu_brand'].map(custom_order)

        #Pasar la variable Ram a categorica
        custom_order = {2: 0, 4: 1, 6: 2, 8: 3, 12: 4, 16: 5, 24: 6, 32: 7, 64: 8}
        X_processed['Ram_encoded'] = X_processed['Ram'].map(custom_order)

        X_processed = X_processed[["Ram_encoded", "Cpu_brand_encoded", "Price"]].copy()
                
        #Retornar los datos
        return X_processed


In [ ]:
class CustomRegression(BaseEstimator, TransformerMixin):
    def init(self):
        self.model = None
        self.coef = None
        self.intercept = None

    def fit(self, X, y=None):
        var_selec = ["Cpu_brand_encoded", "Ram_encoded"]
        X_train, X_test, y_train, y_test = train_test_split(X[var_selec], X["Price"], test_size=0.3, random_state=1)
        
        # Vamos a llevar al mismo dominio las diferentes variables
        mms= StandardScaler()
        # transform data
        Xnorm = mms.fit_transform(X_train[var_selec])
        Xfinal = pd.DataFrame(Xnorm, columns =var_selec)
                
        self.model = LinearRegression()
        self.model.fit(Xfinal, y_train)
        
        self.coef = self.model.coef_
        self.intercept = self.model.intercept_
        
        return self

    def transform(self, X):        

        # Se entrena el modelo con los datos de entrenamiento elegidos
        # self.model.fit(X_train2, y_train2)

        return regression

In [ ]:
custom_preprocessor = CustomPreprocessor()
custom_regression = CustomRegression()
pipeline = Pipeline(
    [
        ("processing", custom_preprocessor),
        ("model", custom_regression)
    ]
)

In [ ]:
# Ajusta el modelo en tus datos transformados
pipeline.fit(df_compu)

In [ ]:
pd.DataFrame({"columns": var_selec, "coef": pipeline["model"].coef})

In [ ]:
pipeline["model"].intercept

Como podemos ver el pipeline creado automatiza todos los pasos de creación del modelo y de el se pueden obtener los resultados requeridos. 

### 10.2. Persisitencia del pipeline 

In [ ]:
filename = "CompuModelo.joblib"
dump(pipeline, filename)

Con el pipeline terminado, se exporta como un archivo el cúal puede ser cargado en cualquier contexto que la empresa necesite y reutilizado para automatizar el proceso de analizar los datos nuevos del contexto del problema de la empresa.

## 11. Predicción de valores

Con la regresión calculada se hara la tarea de predecir los valores de los computadores que la empresa necesita. Para etso se cargaran los datos y estos se le alimentaran al modelo creado el cual producira los valores esperados para estos computadores. 

In [ ]:
#Importar datos a predecir
df_compu_predict=pd.read_csv('./Regresión_data_laptop_data_test_unlabeled.csv', sep=',', encoding = "ISO-8859-1")

Para que la regresión pueda leer los valores estos deben ser transformados a numericos como fue realizado en el preprocesamiento.

In [ ]:
#Preparar la variable Ram para el calculo
custom_order = {2: 0, 4: 1, 6: 2, 8: 3, 12: 4, 16: 5, 24: 6, 32: 7, 64: 8}

df_compu_predict['Ram_encoded'] = df_compu_predict['Ram'].map(custom_order)

In [ ]:
#Preparar la variable procesador para el calculo
label_encoder = LabelEncoder()
custom_order = {'Other Intel Processor': 0, 'AMD Processor': 1, 'Intel Core i3': 2, 'Intel Core i5': 3, 'Intel Core i7': 4}

df_compu_predict['Cpu_brand_encoded'] = df_compu_predict['Cpu_brand'].map(custom_order)

In [ ]:
#Se utiliza el modelo para predecir los precios de interes.
X_predict = df_compu_predict[var_selec]

df_compu_predict.CalculatedPrice = regression.predict(X_predict)

In [ ]:
df_compu_predict.to_csv('resultado_prediccion.csv', index=False)

Con el modelo calculado, se predijeron los datos los cuales fueron reportados en el archivo "resultados_predición.csv". Le recomendamos a la empresa utilizar estos valores predecidos dado que el modelo es efectivo haciendolo. 